<a href="https://colab.research.google.com/github/HuyenNguyenHelen/MyTREC_2021/blob/main/BERT_Innitial_Reranking.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install -U sentence-transformers rank_bm25

     |████████████████████████████████| 92kB 10.6MB/s 
     |████████████████████████████████| 2.5MB 35.9MB/s 
     |████████████████████████████████| 1.2MB 38.2MB/s 
     |████████████████████████████████| 901kB 37.2MB/s 
     |████████████████████████████████| 3.3MB 39.7MB/s 
  Created wheel for sentence-transformers: filename=sentence_transformers-2.0.0-cp37-none-any.whl size=126711 sha256=54aa765e2b7abaee79682c94caff351a829336ffcbad879e378da029a0dd3cde
  Stored in directory: /root/.cache/pip/wheels/38/d2/98/d191289a877a34c68aa67e05179521e060f96394a3e9336be6
Successfully built sentence-transformers
ERROR: transformers 4.8.2 has requirement huggingface-hub==0.0.12, but you'll have huggingface-hub 0.0.13 which is incompatible.


# Documents and Query processing

### Documents

In [5]:
import pandas as pd
path = r'/content/Bhanu_New_Summary_OR_NER-BERN_Query2016_gene-disease-drug_2016-1_5000.csv'
with open(path, 'r', encoding = 'utf-8' ) as f:
    data = pd.read_csv(f, header = None, delimiter='\t')
data.columns = ['queryID','docID', 'score', 'concat_str']
data = data.drop(columns =  ['queryID','score' ] )
data1 = data.drop_duplicates()
set_doc = set(data1['docID'])
set_txt = set(data1['concat_str'])
print(len(data1['docID'].unique()))
print(len(data1['concat_str'].unique()))
print(len(set_doc), len(set_txt))

data1 = data1.drop_duplicates()
print(len(data1))
data1.head()


109696
109674
109696 109674
109696


docID                                         concat_str
0  4391998  avail urea nitrogencreatinin gastrointestin bl...
1  4529650  duoden adenocarcinoma melena duoden melena mic...
2  4798841  preoper cavern hemangioma present melena wirel...
3  3999026  anemia melena pyeloduoden fistula stoneassoci ...
4  3113951  ultrasonograph cow abomas lymphosarcoma descri...

In [6]:

doc_txt = data1['concat_str'].values.tolist()

### Query

In [7]:
#Processed query 2016
path = r"/content/RawQueries_2016.txt"
with open(path, 'r', encoding = 'utf-8' ) as f:
    query_df = pd.read_csv(f, delimiter='\t')
query_df.columns = ['QueryID', 'rawq']
query_df['new_rawq'] = query_df['rawq'].apply(lambda x: ' '.join([i for i in str(x).split(',')]))

query_df.head()


QueryID  ...                                           new_rawq
0        2  ...  arthroplasti present histori femal right snap ...
1        3  ...  day found 96 ua pt blood hypotens rate strepto...
2        4  ...  dm2 87 tachypnea osteoporosi blood anxieti dep...
3        5  ...  day fever 82 previou cough dyspnea man chronic...
4        6  ...  sever femal atrial year cad gallston ct fever ...

[5 rows x 3 columns]

In [ ]:
# # Loading the Query [2016/2021]
# ## Query 2016
# import pandas as pd
# import xml.etree.ElementTree as ET

# tree = ET.parse(r"/content/topics2016.xml")
# root = tree.getroot()

# queryID, note, description, summary=[],[],[], []

 
# i=0
# while i<len(root):
#     queryID.append(i+1)
#     for j in range (len(root[i])):
#         if root[i][j].tag == 'note':
#             note.append(root[i][j].text.replace('\n',''))
#         if root[i][j].tag == 'summary':
#             summary.append(root[i][j].text)
#         if root[i][j].tag == 'description':
#             description.append(root[i][j].text)
  
#     i+=1
    
# query_df = pd.DataFrame(zip(queryID, note, description, summary), columns =['queryID', 'note', 'description', 'summary'] )
# query_df.head()

queryID  ...                                            summary
0        1  ...  A 78 year old male presents with frequent stoo...
1        2  ...  An elderly female with past medical history of...
2        3  ...  A 75F found to be hypoglycemic with hypotensio...
3        4  ...  An 87 yo woman with h/o osteoporosis, DM2, dem...
4        5  ...  An 82 man with multiple chronic conditions and...

[5 rows x 4 columns]

In [8]:
# Processing query
queries = query_df['new_rawq'].values.tolist()

# Question-Answering using Simple Wikipedia Index

This examples demonstrates the setup for Query / Question-Answer-Retrieval.

You can input a query or a question. The script then uses semantic search
to find relevant passages in Simple English Wikipedia (as it is smaller and fits better in RAM).

For semantic search, we use SentenceTransformer('msmarco-distilbert-base-v2') and retrieve
100 potentially passages that answer the input query.

Next, we use a more powerful CrossEncoder (cross_encoder = CrossEncoder('cross-encoder/ms-marco-TinyBERT-L-6')) that
scores the query and all retrieved passages for their relevancy. The cross-encoder is neccessary to filter out certain noise
that might be retrieved from the semantic search step.


In [9]:
import json
from sentence_transformers import SentenceTransformer, CrossEncoder, util
import time
import gzip
import os
import torch

if not torch.cuda.is_available():
    print("Warning: No GPU found. Please add GPU to your notebook")

# We use the Bi-Encoder to encode all passages, so that we can use it with sematic search
model_name = 'msmarco-MiniLM-L-6-v3'
bi_encoder = SentenceTransformer(model_name)


# The bi-encoder will retrieve 100 documents. We use a cross-encoder, to re-rank the results list to improve the quality
cross_encoder = CrossEncoder('cross-encoder/ms-marco-MiniLM-L-6-v2')
        
# Here, we compute the corpus_embeddings from scratch (which can take a while depending on the GPU)
corpus_embeddings = bi_encoder.encode(doc_txt, convert_to_tensor=True, show_progress_bar=True)
print(corpus_embeddings)


tensor([[ 0.3816,  0.0557,  0.1371,  ..., -0.0199,  0.4855,  0.2420],
        [ 0.0024, -0.2993,  0.0318,  ..., -0.3888, -0.2327,  0.1130],
        [ 0.0950,  0.0926,  0.4330,  ..., -0.4781,  0.3871,  0.3569],
        ...,
        [ 0.1529,  0.4988,  0.3126,  ...,  0.0900,  0.3453,  0.7746],
        [-0.1092,  0.0251,  0.3285,  ..., -0.2793,  0.1442,  0.1667],
        [-0.3521,  0.2357,  0.1785,  ..., -0.0533,  0.3596,  0.3839]],
       device='cuda:0')


In [10]:
##### Sematic Search
all_output = []
top_k = 1000

for id, query in zip(query_df['QueryID'], queries):
   
  # Encode the query using the bi-encoder and find potentially relevant passages
    question_embedding = bi_encoder.encode(query, convert_to_tensor=True)
    question_embedding = question_embedding.cuda()
    hits_en = util.semantic_search(question_embedding, corpus_embeddings, top_k=top_k)
    for hit in hits_en:
      tempt_dic = []
      output = {}
      #hit = sorted(hits, key=lambda x: x['score'], reverse=True)
      for h in hit:   
        #temp_dict = {'doc': [], 'score': []}
        tempt_dic.append([data[data['concat_str']==doc_txt[h['corpus_id']]]['docID'].values[0], h['score']] )
        with open('/content/semantic_output_f5k_OR_rawq.txt', "a") as outFile:
            outFile.write(str(id) + "\t" + str(data[data['concat_str']==doc_txt[h['corpus_id']]]['docID'].values[0]) + '\t' + str(h['score']) + "\n")
      output[id] = tempt_dic
      
      
    all_output.append(output)


all_output[0]

{2: [[2448688, 0.5922453999519348],
  [3640922, 0.5782870650291443],
  [2504677, 0.5491393804550171],
  [4545570, 0.4819386303424835],
  [2755121, 0.47633618116378784],
  [2361975, 0.46143636107444763],
  [3597125, 0.45506352186203003],
  [4213520, 0.450851172208786],
  [4661154, 0.450772762298584],
  [3278665, 0.44542399048805237],
  [3445103, 0.44060516357421875],
  [4544332, 0.43323665857315063],
  [3182442, 0.4295138716697693],
  [2850835, 0.4281821548938751],
  [3935779, 0.42477694153785706],
  [3649507, 0.42244458198547363],
  [3421930, 0.4205489158630371],
  [3568025, 0.4194733500480652],
  [3584601, 0.4189656972885132],
  [3443644, 0.41840919852256775],
  [3232250, 0.418247252702713],
  [3092498, 0.4168066382408142],
  [3886399, 0.4158356189727783],
  [3495212, 0.4140778183937073],
  [2504679, 0.41249731183052063],
  [4523950, 0.4123266041278839],
  [4172978, 0.41181617975234985],
  [2762554, 0.4095824062824249],
  [3534547, 0.40808215737342834],
  [2911928, 0.40503451228141785

In [ ]:
#### Cross-encoding retrieval
top_k = 2000  # Number of passages we want to retrieve with the bi-encoder 
for id, query in zip(query_df['QueryID'], queries):

    ##### Sematic Search #####
    # Encode the query using the bi-encoder and find potentially relevant passages
    question_embedding = bi_encoder.encode(query, convert_to_tensor=True)
    question_embedding = question_embedding.cuda()
    hits_cross = util.semantic_search(question_embedding, corpus_embeddings, top_k=top_k)
    for hit in hits_cross:
      print('--------------11111111----------------', hit)
      ##### Re-Ranking #####
      # Now, score all retrieved passages with the cross_encoder
      #print(hit)
      #print([doc_txt[h['corpus_id']] for h in hit])
      cross_inp = [[query, doc_txt[h['corpus_id']]] for h in hit]
      cross_scores = cross_encoder.predict(cross_inp)

      # Sort results by the cross-encoder scores
      for idx in range(len(cross_scores)):
          hit[idx]['cross-score'] = cross_scores[idx]
      print('------222222222222-------', hit)
      tempt_dic = []
      output = {}
      hit = sorted(hit, key=lambda x: x['cross-score'], reverse=True)
      for h in hit:   
        #temp_dict = {'doc': [], 'score': []}
        tempt_dic.append([data[data['concat_str']==doc_txt[h['corpus_id']]]['docID'].values[0], h['cross-score']] )
        with open('/content/rerank_cross_output_f5k_OR_rawq_2k.txt', "a") as outFile:
            outFile.write(str(id) + "\t" + str(data[data['concat_str']==doc_txt[h['corpus_id']]]['docID'].values[0]) + '\t' + str(h['cross-score']) + "\n")
      output[id] = tempt_dic



#     hits_re = sorted(hits, key=lambda x: x['cross-score'], reverse=True)
#     for hit in hits_re[0:3]:
#         print("\t{:.3f}\t{}".format(hit['cross-score'], doc_txt[hit['corpus_id']].replace("\n", " ")))
#     #return hits_re['cross-score'], doc_txt[int(hits_re['corpus_id'])]
      

--------------11111111---------------- [{'corpus_id': 4121, 'score': 0.5922453999519348}, {'corpus_id': 1697, 'score': 0.5782870650291443}, {'corpus_id': 605, 'score': 0.5491393804550171}, {'corpus_id': 1148, 'score': 0.4819386303424835}, {'corpus_id': 993, 'score': 0.47633618116378784}, {'corpus_id': 621, 'score': 0.46143636107444763}, {'corpus_id': 546, 'score': 0.45506352186203003}, {'corpus_id': 107076, 'score': 0.450851172208786}, {'corpus_id': 4557, 'score': 0.450772762298584}, {'corpus_id': 1286, 'score': 0.44542399048805237}, {'corpus_id': 3999, 'score': 0.44060516357421875}, {'corpus_id': 979, 'score': 0.43323665857315063}, {'corpus_id': 2646, 'score': 0.4295138716697693}, {'corpus_id': 100289, 'score': 0.4281821548938751}, {'corpus_id': 4277, 'score': 0.42477694153785706}, {'corpus_id': 591, 'score': 0.42244458198547363}, {'corpus_id': 738, 'score': 0.4205489158630371}, {'corpus_id': 998, 'score': 0.4194733500480652}, {'corpus_id': 717, 'score': 0.4189656972885132}, {'corpus_

In [ ]:
# This function will search all wikipedia articles for passages that
# answer the query
# def search(query):

#     ##### Sematic Search #####
#     # Encode the query using the bi-encoder and find potentially relevant passages
#     question_embedding = bi_encoder.encode(query, convert_to_tensor=True)
#     question_embedding = question_embedding.cuda()
#     hits = util.semantic_search(question_embedding, corpus_embeddings, top_k=top_k)
#     hits = hits[0]  # Get the hits for the first query

#     ##### Re-Ranking #####
#     # Now, score all retrieved passages with the cross_encoder
#     cross_inp = [[query, doc_txt[hit['corpus_id']]] for hit in hits]
#     cross_scores = cross_encoder.predict(cross_inp)

#     # Sort results by the cross-encoder scores
#     for idx in range(len(cross_scores)):
#         hits[idx]['cross-score'] = cross_scores[idx]

#     # Output of top-5 hits from bi-encoder
#     print("\n-------------------------\n")
#     print("Top-3 Bi-Encoder Retrieval hits")
#     hits_en = sorted(hits, key=lambda x: x['score'], reverse=True)
#     for hit in hits_en[0:3]:
#          print("\t{:.3f}\t{}".format(hit['score'], doc_txt[hit['corpus_id']].replace("\n", " ")))

#     # Output of top-5 hits from re-ranker
#     print("\n-------------------------\n")
#     print("Top-3 Cross-Encoder Re-ranker hits")
#     hits_re = sorted(hits, key=lambda x: x['cross-score'], reverse=True)
#     for hit in hits_re[0:3]:
#         print("\t{:.3f}\t{}".format(hit['cross-score'], doc_txt[hit['corpus_id']].replace("\n", " ")))
#     #return hits_re['cross-score'], doc_txt[int(hits_re['corpus_id'])]




